**Enoncé Projet 3** : Voici une vision globale des étapes techniques pour un premier moyen de transport (par exemple les bornes de vélos en libre-service) : Récupération par fichier plat des données unitaires et affichage d’une carte Collecte via une API des données unitaires et mise à jour de la carte Automatisation toutes les 15 minutes de la collecte via API et stockage de cet historique dans une base de données

Suivant l’heure du jour, vous verrez une sorte de “respiration”, en fonction des lieux de sorties, des quartiers de bureaux ou des zones résidentielles.

Puis, vous pourrez ajouter un second moyen de transport, etc...

Suivant les villes il y a des bornes de comptage sur les voies cyclables, et de trafic sur les voies rapides Concernant les transports en commun, vous obtiendrez la fréquence de desserte, mais vous n’avez généralement pas accès aux données sur la fréquentation (nombre d’usagers)

Pour automatiser la collecte, votre formateur vous donnera accès à une quête nommée “schedule”. Dans un process réel en entreprise, vous pourriez payer pour un serveur cloud. Ici, un ordinateur d’un membre du groupe pourra jouer le rôle de serveur, il faudra le faire tourner pendant minimum 48h pour avoir des résultats représentatifs.


###**Objectifs**
1. Automatiser la collecte de données afin de se constituer un historique de données (ex: connaître toutes les heures de passage des bus de la ligne 141 sur une journée, ou une période donnée)
2. Le faire d'abord pour un moyen de transport donné, puis étendre notre dataset en retenant d'autres moyens de transport
3. Visualiser par heure du jour via une map la densité du trafic

NB : Collecte toutes les 15min et pendant 48h (via library Schedule)

###**Ressources**

- https://www.data.gouv.fr/fr/organizations/rennes-metropole-en-acces-libre-1/#/datasets -> comptage vélos et piétons ++ état du trafic en temps réel
- https://www.data.gouv.fr/fr/datasets/prochains-passages-des-lignes-de-bus-du-reseau-star-en-temps-reel/ -> fichiers csv avec passages bus temps réel
- https://data.explore.star.fr/explore/dataset/tco-bus-circulation-passages-tr/api/ -> datasource API pour requêter directement les données en temps réel des prochains passages des bus
- https://data.explore.star.fr/api/explore/v2.1/catalog/datasets/tco-bus-circulation-passages-tr/records?limit=20&refine=idligne%3A%220001%22 -> API RENNES pour le "nomcourtligne": "C1"

# **REQUÊTAGE DES DONNEES API ET AUTOMATISATION**

In [ ]:
#LES LINKS APIS
# https://data.explore.star.fr/api/explore/v2.1/catalog/datasets/tco-bus-circulation-passages-tr/records?limit=20&refine=idligne%3A%220001%22
# https://data.explore.star.fr/api/explore/v2.1/catalog/datasets/tco-bus-circulation-passages-tr/records?limit=20&refine=idligne%3A%220002%22
# https://data.explore.star.fr/api/explore/v2.1/catalog/datasets/tco-bus-circulation-passages-tr/records?limit=20&refine=idligne%3A%220003%22
# https://data.explore.star.fr/api/explore/v2.1/catalog/datasets/tco-bus-circulation-passages-tr/records?limit=20&refine=idligne%3A%220004%22
# https://data.explore.star.fr/api/explore/v2.1/catalog/datasets/tco-bus-circulation-passages-tr/records?limit=20&refine=idligne%3A%220005%22

In [ ]:
### ETAPE 0 => ON GENERE AUTOMATIQUEMENT LES URLS DES DIFFERENTES SOURCE API (TÂCHE A REALISER 1 FOIS)

# URL de base - data bus ---> rem. : Au lieu de limit=20 on change par limit=-1 pour récupérer l'exhaustivité des données disponibles dans l'API propre à chaque ligne (sinon 20 par défaut)
base_url = "https://data.explore.star.fr/api/explore/v2.1/catalog/datasets/tco-bus-circulation-passages-tr/records?limit=-1&refine=idligne%3A%22"

# Liste pour stocker les URLs générées
urls = []

# Boucle pour générer les URLs de 1 à 200 ## PARAMETRE A MODIFIER SI BESOIN /!\
for i in range(1, 201):
    # Formatage du numéro de ligne avec zéro(s) devant
    line_number = str(i).zfill(4)

    # Construire l'URL complète
    url = f"{base_url}{line_number}%22"

    # Ajouter l'URL à la liste
    urls.append(url)

# Affichage des URLs générées
for url in urls:
    print(url)

https://data.explore.star.fr/api/explore/v2.1/catalog/datasets/tco-bus-circulation-passages-tr/records?limit=-1&refine=idligne%3A%220001%22
https://data.explore.star.fr/api/explore/v2.1/catalog/datasets/tco-bus-circulation-passages-tr/records?limit=-1&refine=idligne%3A%220002%22
https://data.explore.star.fr/api/explore/v2.1/catalog/datasets/tco-bus-circulation-passages-tr/records?limit=-1&refine=idligne%3A%220003%22
https://data.explore.star.fr/api/explore/v2.1/catalog/datasets/tco-bus-circulation-passages-tr/records?limit=-1&refine=idligne%3A%220004%22
https://data.explore.star.fr/api/explore/v2.1/catalog/datasets/tco-bus-circulation-passages-tr/records?limit=-1&refine=idligne%3A%220005%22
https://data.explore.star.fr/api/explore/v2.1/catalog/datasets/tco-bus-circulation-passages-tr/records?limit=-1&refine=idligne%3A%220006%22
https://data.explore.star.fr/api/explore/v2.1/catalog/datasets/tco-bus-circulation-passages-tr/records?limit=-1&refine=idligne%3A%220007%22
https://data.explore

In [ ]:
### ETAPE 1 => FONCTION DE REQUÊTAGE POUR UN LIEN API (SOIT POUR UNE SEULE LIGNE DE BUS)

import requests
import pandas as pd

# # List of API endpoints
# urls = [
#     "https://data.explore.star.fr/api/explore/v2.1/catalog/datasets/tco-bus-circulation-passages-tr/records?limit=20&refine=idligne%3A%220001%22",
#     "https://data.explore.star.fr/api/explore/v2.1/catalog/datasets/tco-bus-circulation-passages-tr/records?limit=20&refine=idligne%3A%220002%22",
#     "https://data.explore.star.fr/api/explore/v2.1/catalog/datasets/tco-bus-circulation-passages-tr/records?limit=20&refine=idligne%3A%220003%22",
#     "https://data.explore.star.fr/api/explore/v2.1/catalog/datasets/tco-bus-circulation-passages-tr/records?limit=20&refine=idligne%3A%220004%22",
#     "https://data.explore.star.fr/api/explore/v2.1/catalog/datasets/tco-bus-circulation-passages-tr/records?limit=20&refine=idligne%3A%220005%22"
# ]

## Fonction qui récupère et traite les données API pour une ligne de bus
## => Démarche = requêtage données format json et implémentation dans une liste processed_data + définition de la structure générale du dictionnaire imbriqué + conversion de la liste finale en dataframe

def fetch_and_process_data(url):
    response = requests.get(url).json()
    data = response['results']
    # Process data (e.g., extract relevant fields)
    processed_data = []
    for entry in data:
        processed_entry = {
            'idligne': entry.get('idligne'),
            'nomcourtligne': entry.get('nomcourtligne'),
            'sens': entry.get('sens'),
            'destination': entry.get('destination'),
            'idarret': entry.get('idarret'),
            'nomarret': entry.get('nomarret'),
            'lon': entry['coordonnees'].get('lon') if 'coordonnees' in entry else None,
            'lat': entry['coordonnees'].get('lat') if 'coordonnees' in entry else None,
            'arriveetheorique': entry.get('arriveetheorique'),
            'departtheorique': entry.get('departtheorique'),
            'arrivee': entry.get('arrivee'),
            'depart': entry.get('depart'),
            'idcourse': entry.get('idcourse'),
            'precision': entry.get('precision'),
            'visibilite': entry.get('visibilite'),
            'heureextraction': entry.get('heureextraction')
        }
        processed_data.append(processed_entry)
    return pd.DataFrame(processed_data)



# ## => Démarche = On teste la fonction 'fetch_and_process_data' pour chaque url =>

# for i, url in enumerate(urls, start=1):
#     df = fetch_and_process_data(url)
#     print(f"Data from URL {i}: {len(df)}")
#     display(df.head())  # Print the first few rows of the DataFrame

In [ ]:
### ETAPE 2 => FONCTION DE CONCATENATION DES DONNEES APRES REQUÊTAGE DES DIFFERENTES URLS (SOIT DE L'ENSEMBLE DES LIGNES DE BUS)
### Démarche => on appelle la fonction 'fetch_and_process_data' précédemment créée en étape 1 pour chaque urls disponible et générée en étape 0

def fetch_and_concat_data(urls):
    """
    Récupère les données à partir de plusieurs URLs, les concatène et retourne un DataFrame unique.

    :param urls: Liste d'URLs à requêter
    :return: DataFrame combiné
    """
    # Initialiser une liste pour stocker les DataFrames
    dataframes = []

    # Boucle sur les URLs pour récupérer et traiter les données
    for i, url in enumerate(urls):
        try:
            # Récupérer et traiter les données de chaque URL via la fonction fetch_and_process_data créée à l'étape 1
            df = fetch_and_process_data(url)
            dataframes.append(df)
        except Exception as e:
            print(f"Erreur lors de la requête pour l'URL {url}: {e}")

    # Concaténer tous les DataFrames dans un DataFrame unique
    combined_df = pd.concat(dataframes, ignore_index=True)

    return combined_df

In [ ]:
### ETAPE 3 => FONCTION DE SAUVEGARDE DE TTES LES DONNEES PRECEDEMMENT REQUÊTEES DANS UN FICHIER .CSV OU .TXT POUR CONSTITUER UN HISTORIQUE DE DONNEES (obj : 48h de données requêtées toutes les 15min)
### Démarche => on génère un horodatage qu'on implémente dans le nom du fichier .csv de requêtage et stockage, en prévision du stockage répété pendant 48h pour distinguer l'ensemble des fichiers .csv
### /!\ FONCTIONNE EN LOCAL UNIQUEMENT AUTREMENT DIT SUR JUPYTER NOTEBOOK

from datetime import datetime

def save_dataframe_with_timestamp(df, file_format='csv'): ## où df est le dataframe à sauvegarder et file_format='csv' le format du fichier de sortie généré // format .txt possible

    # Générer un horodatage sous forme de string
    timestamp = datetime.now().strftime("%Y%m%d_%H%M%S")  # Format YYYYMMDD_HHMMSS

    # Nom du fichier avec horodatage
    file_name = f"bus_data_{timestamp}"

    if file_format == 'csv':
        df.to_csv(f"{file_name}.csv", index=False, sep=',', encoding='utf-8')
        print(f"DataFrame sauvegardé en fichier {file_name}.csv")

    elif file_format == 'txt':
        df.to_csv(f"{file_name}.txt", index=False, sep='\t', encoding='utf-8')
        print(f"DataFrame sauvegardé en fichier {file_name}.txt")

    else:
        print(f"Format non supporté : {file_format}. Utilisez 'csv' ou 'txt'.")

# ## Test bon fonctionnement fonction
# save_dataframe_with_timestamp(combined_df, 'csv')  # Sauvegarder en CSV avec horodatage

In [ ]:
### ETAPE 4 => ON TESTE L'ENCHAÎNEMENT DES FONCTIONS DES ETAPES 0,1,2,3 AVANT DE POUVOIR METTRE EN OEUVRE SCHEDULE POUR LA REPETITION DES TÂCHES 1,2,3 A INSTANT DONNE (OBJ : TOUTES LES 15 MIN PDT 48H)

import os
print(os.getcwd()) ## permet d'afficher le répertoire de travail en local où seront stockés les fichiers de sortie (données requêtées)

df_test = fetch_and_process_data(url) ## exécution ETAPE 1 à partir de url de départ
df_combined_test = fetch_and_concat_data(urls) ## exécution ETAPE 2 à partir de l'ensemble des urls générées en ETAPE 0
print(f"taille df_test: {len(df_test)}") ## à supp car pas très utile puisque donne l'info pour le dernier df dispo (i.e. dernière ligne de bus requêtée)
print(f"taille df_combined_test: {len(df_combined_test)}") ## permet d'indiquer la taille du df consolidé
# display(df_combined_test.head())
# print(df_combined_test["nomcourtligne"].unique()) ## permet de lister toutes les lignes de bus requêtées

## créer un dictionnaire avec toutes les lignes de bus requêtées et le nombre de données collectées pour chaque :
rslt_dict = dict(df_combined_test["nomcourtligne"].value_counts())
print(f"Nombre de données collectées par ligne de bus : {rslt_dict}")
print(f"Nombre de lignes de bus collectées : {len(rslt_dict)}")
# display(df_combined_test["nomcourtligne"].value_counts()) ## permet d'indiquer le volume de données requêtées pour chaque ligne de bus
save_dataframe_with_timestamp(df_combined_test, 'csv') ## permet de sauvegarder les données précédemment requêtées

/content
taille df_test: 0
taille df_combined_test: 3875
Nombre de données collectées par ligne de bus : {'C1': 100, '53': 100, '55': 100, 'C2': 100, '59': 100, '61': 100, '62': 100, '64': 100, '65': 100, '67': 100, '68': 100, '71': 100, '72': 100, '74': 100, '76': 100, '77': 100, '78': 100, '54': 100, '56': 100, '52': 100, '12': 100, 'C3': 100, 'C4': 100, 'C5': 100, 'C6': 100, '51': 100, '10': 100, '11': 100, 'C7': 100, '13': 100, '14': 100, '32': 100, '34': 100, '50': 100, '73': 96, '91': 75, '75': 51, '81': 50, '80': 42, '82': 38, '39': 35, '161ex': 27, '70': 26, '37': 22, '79': 13}
Nombre de lignes de bus collectées : 45
DataFrame sauvegardé en fichier bus_data_20240913_085811.csv


In [ ]:
### ETAPE 5 => IMPORT DE LA LIBRAIRIE SCHEDULE POUR AUTOMATISER LA REPETITION PERIODIQUE DES TÂCHES 1,2,3 (OBJ = TOUTES LES 15 MIN PDT 48H)
### Démarche => on créée une fonction 'job' qui enchaine les 3 fonctions précédemment créées en Etapes 1,2,3 et qu'on appelle via schedule toutes les 15 min pour répétition du requêtage et stockage en .csv

!pip install schedule
import schedule
import time

def job():
    """
    Fonction de tâche à exécuter toutes les 15 minutes.
    """
    df = fetch_and_process_data(url)
    df_combined = fetch_and_concat_data(urls)
    save_dataframe_with_timestamp(df_combined, 'csv')

# Planifier la tâche toutes les 15 minutes
schedule.every(15).minutes.do(job)

# Boucle infinie pour exécuter le scheduler
while True:
    schedule.run_pending()
    time.sleep(1)  # Pause de 1 seconde avant de vérifier la prochaine tâche

#**EXPLORATION DES DONNEES ET VISUELS**

In [ ]:
combined_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 5043 entries, 0 to 5042
Data columns (total 18 columns):
 #   Column            Non-Null Count  Dtype  
---  ------            --------------  -----  
 0   idligne           5043 non-null   object 
 1   nomcourtligne     5043 non-null   object 
 2   sens              5043 non-null   int64  
 3   destination       5043 non-null   object 
 4   idarret           5043 non-null   object 
 5   nomarret          5043 non-null   object 
 6   lon               5043 non-null   float64
 7   lat               5043 non-null   float64
 8   arriveetheorique  5043 non-null   object 
 9   departtheorique   5043 non-null   object 
 10  arrivee           5043 non-null   object 
 11  depart            5043 non-null   object 
 12  idcourse          5043 non-null   object 
 13  idbus             529 non-null    object 
 14  numerobus         529 non-null    float64
 15  precision         5043 non-null   object 
 16  visibilite        5043 non-null   object 


In [ ]:
import pandas as pd
import folium
# Create a Folium map centered around the mean latitude and longitude of the combined DataFrame
map_center = [combined_df['lat'].mean(), combined_df['lon'].mean()]
m = folium.Map(location=map_center, zoom_start=12)

# Add markers to the map
for idx, row in combined_df.iterrows():
    if pd.notna(row['lat']) and pd.notna(row['lon']):
        folium.Marker(
            location=[row['lat'], row['lon']],
            popup=f"Line: {row['idligne']}<br>Stop: {row['nomarret']}",
            icon=folium.Icon(color='blue', icon='info-sign')
        ).add_to(m)

# Save the map to an HTML file
m.save('bus_stops_map.html')

# If running in a Jupyter notebook, you can display the map inline
m

In [ ]:
# ### SI STOCKAGE DONNEES EN FORMAT SQLITE /// A VOIR SI ON APPROFONDIE LA PISTE

# from sqlalchemy import create_engine

# # Create a SQLite engine
# engine = create_engine('sqlite:///transport_data.db', echo=True)

# # Store the DataFrame into a SQL table
# combined_df.to_sql('bus_data', con=engine, if_exists='append', index=False)

In [ ]:
# ### A VOIR SI ON CONSERVE ?? /// SCHEDULE DEVRAIT SUFFIRE

# !pip install apscheduler
# from apscheduler.schedulers.blocking import BlockingScheduler
# import datetime

# # Scheduler setup
# scheduler = BlockingScheduler()

# # Define a job to fetch data and store it in the database
# def scheduled_job():
#     print(f"Fetching data at {datetime.datetime.now()}")
#     dataframes = [fetch_and_process_data(url) for url in urls]
#     combined_df = pd.concat(dataframes, ignore_index=True)
#     combined_df.to_sql('bus_data', con=engine, if_exists='append', index=False)
#     print("Data successfully saved to database")

# # Schedule the job every 15 minutes
# scheduler.add_job(scheduled_job, 'interval', minutes=15)

# # Start the scheduler
# print("Scheduler started. Press Ctrl+C to exit.")
# try:
#     scheduler.start()
# except (KeyboardInterrupt, SystemExit):
#     pass

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 59.3/59.3 kB 913.1 kB/s eta 0:00:00
Scheduler started. Press Ctrl+C to exit.
Fetching data at 2024-09-12 14:35:00.157689


In [ ]:
# !pip install schedule
# from sqlalchemy import create_engine, Table, Column, Float, Integer, String, MetaData
# import schedule
# import time
# import datetime

In [ ]:
# !pip install apscheduler
# import requests
# import pandas as pd
# from sqlalchemy import create_engine, Table, Column, Float, Integer, String, MetaData
# from apscheduler.schedulers.blocking import BlockingScheduler # This line imports the BlockingScheduler class from the apscheduler.schedulers.blocking module
# import datetime

# # List of API endpoints
# urls = [
#     "https://data.explore.star.fr/api/explore/v2.1/catalog/datasets/tco-bus-circulation-passages-tr/records?limit=20&refine=idligne%3A%220001%22",
#     "https://data.explore.star.fr/api/explore/v2.1/catalog/datasets/tco-bus-circulation-passages-tr/records?limit=20&refine=idligne%3A%220002%22",
#     "https://data.explore.star.fr/api/explore/v2.1/catalog/datasets/tco-bus-circulation-passages-tr/records?limit=20&refine=idligne%3A%220003%22",
#     "https://data.explore.star.fr/api/explore/v2.1/catalog/datasets/tco-bus-circulation-passages-tr/records?limit=20&refine=idligne%3A%220004%22",
#     "https://data.explore.star.fr/api/explore/v2.1/catalog/datasets/tco-bus-circulation-passages-tr/records?limit=20&refine=idligne%3A%220005%22"
# ]

# # Database setup
# DATABASE_URL = 'sqlite:///bus_data.db'
# engine = create_engine(DATABASE_URL)
# metadata = MetaData()

# # Define table structure
# bus_stops = Table('bus_stops', metadata,
#     Column('id', Integer, primary_key=True, autoincrement=True),
#     Column('idligne', String),
#     Column('nomcourtligne', String),
#     Column('sens', String),
#     Column('destination', String),
#     Column('idarret', String),
#     Column('nomarret', String),
#     Column('lon', Float),
#     Column('lat', Float),
#     Column('arriveetheorique', String),
#     Column('departtheorique', String),
#     Column('arrivee', String),
#     Column('depart', String),
#     Column('idcourse', String),
#     Column('idbus', String),
#     Column('numerobus', String),
#     Column('precision', String),
#     Column('visibilite', String),
#     Column('heureextraction', String),
#     Column('timestamp', String)
# )

# metadata.create_all(engine)

# # Function to fetch and process data from a URL
# def fetch_and_process_data(url):
#     response = requests.get(url).json()
#     data = response['results']
#     processed_data = []
#     for entry in data:
#         processed_entry = {
#             'idligne': entry.get('idligne'),
#             'nomcourtligne': entry.get('nomcourtligne'),
#             'sens': entry.get('sens'),
#             'destination': entry.get('destination'),
#             'idarret': entry.get('idarret'),
#             'nomarret': entry.get('nomarret'),
#             'lon': entry['coordonnees'].get('lon') if 'coordonnees' in entry else None,
#             'lat': entry['coordonnees'].get('lat') if 'coordonnees' in entry else None,
#             'arriveetheorique': entry.get('arriveetheorique'),
#             'departtheorique': entry.get('departtheorique'),
#             'arrivee': entry.get('arrivee'),
#             'depart': entry.get('depart'),
#             'idcourse': entry.get('idcourse'),
#             'idbus': entry.get('idbus'),
#             'numerobus': entry.get('numerobus'),
#             'precision': entry.get('precision'),
#             'visibilite': entry.get('visibilite'),
#             'heureextraction': entry.get('heureextraction'),
#             'timestamp': datetime.datetime.now().isoformat()
#         }
#         processed_data.append(processed_entry)
#     return processed_data

# # Function to update the database
# def update_database():
#     all_data = []
#     for url in urls:
#         data = fetch_and_process_data(url)
#         all_data.extend(data)

#     df = pd.DataFrame(all_data)
#     df.to_sql('bus_stops', con=engine, if_exists='append', index=False)
#     print(f"Data collected and stored at {datetime.datetime.now()}")

# # Scheduler setup
# scheduler = BlockingScheduler()
# scheduler.add_job(update_database, 'interval', minutes=15)

# # Start the scheduler
# print("Scheduler started. Data collection every 15 minutes.")
# scheduler.start()

In [ ]:
# Lire le fichier / import des données [suppose d'enrgistrer le fichier .csv dans le drive perso de chacune directement à la racine]
import pandas as pd
from google.colab import drive
drive.mount('/content/drive')
df = pd.read_csv("/content/drive/My Drive/bus_data_20240913_052550.csv")
# Affiche les premières lignes du DataFrame
#display(df.head(100))

df2 = pd.read_csv("/content/drive/My Drive/bus_data_20240913_054959.csv")

df_concate = pd.concat([df, df2])
#display(df_concate)

# Création d'un mask
mask = df_concate['nomcourtligne'] == 'C1'
display(df_concate[mask])

# Création d'un df C1
df_C1 = df_concate[mask]

#
print(df_C1['idcourse'].nunique())

display(df_C1['idcourse'].value_counts())

df_C1['heureextraction'].groupby(df_C1['idcourse']).value_counts()

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


idligne nomcourtligne  sens destination  idarret           nomarret  \
0         1            C1     0   Chantepie     2842              Nobel   
1         1            C1     0   Chantepie     2806       Vivier Louis   
2         1            C1     0   Chantepie     2809         Discalceat   
3         1            C1     0   Chantepie     2815          La Plesse   
4         1            C1     0   Chantepie     1101        Trois Croix   
..      ...           ...   ...         ...      ...                ...   
95        1            C1     0   Chantepie     1317  Villebois-Mareuil   
96        1            C1     0   Chantepie     2804          Ricoquais   
97        1            C1     0   Chantepie     2805              Camus   
98        1            C1     0   Chantepie     1044     Pierre Legrand   
99        1            C1     0   Chantepie     1046     Anatole France   

         lon        lat           arriveetheorique            departtheorique  \
0  -1.672074  48.158113  2024-09-13T05:11:00+00:00  2024-09-13T05:11:00+00:00   
1  -1.685578  48.159027  2024-09-13T05:14:00+00:00  2024-09-13T05:14:00+00:00   
2  -1.686723  48.154339  2024-09-13T05:17:00+00:00  2024-09-13T05:17:00+00:00   
3  -1.686391  48.137081  2024-09-13T05:22:00+00:00  2024-09-13T05:22:00+00:00   
4  -1.683260  48.127266  2024-09-13T05:25:00+00:00  2024-09-13T05:25:00+00:00   
..       ...        ...                        ...                        ...   
95 -1.649415  48.100101  2024-09-13T06:38:00+00:00  2024-09-13T06:38:00+00:00   
96 -1.676666  48.159105  2024-09-13T04:56:00+00:00  2024-09-13T04:56:00+00:00   
97 -1.681369  48.159116  2024-09-13T04:57:00+00:00  2024-09-13T04:57:00+00:00   
98 -1.685924  48.122179  2024-09-13T05:11:00+00:00  2024-09-13T05:11:00+00:00   
99 -1.689403  48.118240  2024-09-13T05:12:00+00:00  2024-09-13T05:12:00+00:00   

                      arrivee                     depart   idcourse  idbus  \
0   2024-09-13T05:11:00+00:00  2024-09-13T05:11:00+00:00  268435499    NaN   
1   2024-09-13T05:14:00+00:00  2024-09-13T05:14:00+00:00  268435499    NaN   
2   2024-09-13T05:17:00+00:00  2024-09-13T05:17:00+00:00  268435499    NaN   
3   2024-09-13T05:22:00+00:00  2024-09-13T05:22:00+00:00  268435499    NaN   
4   2024-09-13T05:25:00+00:00  2024-09-13T05:25:00+00:00  268435499    NaN   
..                        ...                        ...        ...    ...   
95  2024-09-13T06:38:00+00:00  2024-09-13T06:38:00+00:00  268435622    NaN   
96  2024-09-13T04:56:00+00:00  2024-09-13T04:56:00+00:00  268435635    NaN   
97  2024-09-13T04:57:00+00:00  2024-09-13T04:57:00+00:00  268435635    NaN   
98  2024-09-13T05:11:00+00:00  2024-09-13T05:11:00+00:00  268435635    NaN   
99  2024-09-13T05:12:00+00:00  2024-09-13T05:12:00+00:00  268435635    NaN   

    numerobus   precision    visibilite heureextraction  
0         NaN  Applicable  Grand public        05:15:13  
1         NaN  Applicable  Grand public        05:15:13  
2         NaN  Applicable  Grand public        05:15:13  
3         NaN  Applicable  Grand public        05:15:13  
4         NaN  Applicable  Grand public        05:15:13  
..        ...         ...           ...             ...  
95        NaN  Applicable  Grand public        05:39:09  
96        NaN  Applicable  Grand public        05:39:09  
97        NaN  Applicable  Grand public        05:39:09  
98        NaN  Applicable  Grand public        05:39:09  
99        NaN  Applicable  Grand public        05:39:09  

[200 rows x 18 columns]

11


idcourse
268435509    37
268435504    26
268435526    24
268435499    23
268435518    19
268435622    19
268435635    18
268435514    17
268435539    12
268435506     4
268435552     1
Name: count, dtype: int64

idcourse   heureextraction
268435499  05:15:13           15
           05:39:09            8
268435504  05:39:09           14
           05:15:13           12
268435506  05:39:09            4
268435509  05:15:13           21
           05:39:09           16
268435514  05:39:09           12
           05:15:13            5
268435518  05:39:09           14
           05:15:13            5
268435526  05:15:13           14
           05:39:09           10
268435539  05:15:13            6
           05:39:09            6
268435552  05:39:09            1
268435622  05:39:09           11
           05:15:13            8
268435635  05:15:13           14
           05:39:09            4
Name: count, dtype: int64

In [ ]:
mask2 = df_C1['idcourse'] == 268435635
df_mask2 = df_C1[mask2]
display(df_mask2)

print(df_mask2['nomarret'].value_counts())

idligne nomcourtligne  sens destination  idarret            nomarret  \
86        1            C1     0   Chantepie     2844        Champ Daguet   
87        1            C1     0   Chantepie     2806        Vivier Louis   
88        1            C1     0   Chantepie     2812               Forge   
89        1            C1     0   Chantepie     2813          Haut Trait   
90        1            C1     0   Chantepie     2817  CHP Saint-Grégoire   
91        1            C1     0   Chantepie     1101         Trois Croix   
92        1            C1     0   Chantepie     1042      Cimetière Nord   
93        1            C1     0   Chantepie     1046      Anatole France   
94        1            C1     0   Chantepie     1047           La Touche   
95        1            C1     0   Chantepie     1050           Les Lices   
96        1            C1     0   Chantepie     1085             Laënnec   
97        1            C1     0   Chantepie     1243  Croix Saint-Hélier   
98        1            C1     0   Chantepie     1316              Raison   
99        1            C1     0   Chantepie     1317   Villebois-Mareuil   
96        1            C1     0   Chantepie     2804           Ricoquais   
97        1            C1     0   Chantepie     2805               Camus   
98        1            C1     0   Chantepie     1044      Pierre Legrand   
99        1            C1     0   Chantepie     1046      Anatole France   

         lon        lat           arriveetheorique            departtheorique  \
86 -1.671435  48.155286  2024-09-13T04:54:00+00:00  2024-09-13T04:54:00+00:00   
87 -1.685578  48.159027  2024-09-13T04:58:00+00:00  2024-09-13T04:58:00+00:00   
88 -1.685834  48.150852  2024-09-13T05:01:00+00:00  2024-09-13T05:01:00+00:00   
89 -1.686162  48.147437  2024-09-13T05:02:00+00:00  2024-09-13T05:02:00+00:00   
90 -1.686672  48.142924  2024-09-13T05:03:00+00:00  2024-09-13T05:03:00+00:00   
91 -1.683260  48.127266  2024-09-13T05:08:00+00:00  2024-09-13T05:08:00+00:00   
92 -1.681724  48.123939  2024-09-13T05:09:00+00:00  2024-09-13T05:09:00+00:00   
93 -1.689403  48.118240  2024-09-13T05:12:00+00:00  2024-09-13T05:12:00+00:00   
94 -1.691288  48.116120  2024-09-13T05:13:00+00:00  2024-09-13T05:13:00+00:00   
95 -1.686999  48.111647  2024-09-13T05:18:00+00:00  2024-09-13T05:18:00+00:00   
96 -1.665472  48.104694  2024-09-13T05:29:00+00:00  2024-09-13T05:29:00+00:00   
97 -1.661094  48.102515  2024-09-13T05:31:00+00:00  2024-09-13T05:31:00+00:00   
98 -1.652938  48.101171  2024-09-13T05:33:00+00:00  2024-09-13T05:33:00+00:00   
99 -1.649415  48.100101  2024-09-13T05:34:00+00:00  2024-09-13T05:34:00+00:00   
96 -1.676666  48.159105  2024-09-13T04:56:00+00:00  2024-09-13T04:56:00+00:00   
97 -1.681369  48.159116  2024-09-13T04:57:00+00:00  2024-09-13T04:57:00+00:00   
98 -1.685924  48.122179  2024-09-13T05:11:00+00:00  2024-09-13T05:11:00+00:00   
99 -1.689403  48.118240  2024-09-13T05:12:00+00:00  2024-09-13T05:12:00+00:00   

                      arrivee                     depart   idcourse  idbus  \
86  2024-09-13T04:49:00+00:00  2024-09-13T04:54:00+00:00  268435635    NaN   
87  2024-09-13T04:58:00+00:00  2024-09-13T04:58:00+00:00  268435635    NaN   
88  2024-09-13T05:01:00+00:00  2024-09-13T05:01:00+00:00  268435635    NaN   
89  2024-09-13T05:02:00+00:00  2024-09-13T05:02:00+00:00  268435635    NaN   
90  2024-09-13T05:03:00+00:00  2024-09-13T05:03:00+00:00  268435635    NaN   
91  2024-09-13T05:08:00+00:00  2024-09-13T05:08:00+00:00  268435635    NaN   
92  2024-09-13T05:09:00+00:00  2024-09-13T05:09:00+00:00  268435635    NaN   
93  2024-09-13T05:12:00+00:00  2024-09-13T05:12:00+00:00  268435635    NaN   
94  2024-09-13T05:13:00+00:00  2024-09-13T05:13:00+00:00  268435635    NaN   
95  2024-09-13T05:18:00+00:00  2024-09-13T05:18:00+00:00  268435635    NaN   
96  2024-09-13T05:29:00+00:00  2024-09-13T05:29:00+00:00  268435635    NaN   
97  2024-09-13T05:31:00+00:00  2024-09-13T05:31:00+00:00  268435635    NaN   
98  2

nomarret
Anatole France        2
Champ Daguet          1
Les Lices             1
Camus                 1
Ricoquais             1
Villebois-Mareuil     1
Raison                1
Croix Saint-Hélier    1
Laënnec               1
La Touche             1
Vivier Louis          1
Cimetière Nord        1
Trois Croix           1
CHP Saint-Grégoire    1
Haut Trait            1
Forge                 1
Pierre Legrand        1
Name: count, dtype: int64


In [ ]:
df_C1.info()

<class 'pandas.core.frame.DataFrame'>
Index: 200 entries, 0 to 99
Data columns (total 18 columns):
 #   Column            Non-Null Count  Dtype  
---  ------            --------------  -----  
 0   idligne           200 non-null    int64  
 1   nomcourtligne     200 non-null    object 
 2   sens              200 non-null    int64  
 3   destination       200 non-null    object 
 4   idarret           200 non-null    int64  
 5   nomarret          200 non-null    object 
 6   lon               200 non-null    float64
 7   lat               200 non-null    float64
 8   arriveetheorique  200 non-null    object 
 9   departtheorique   200 non-null    object 
 10  arrivee           200 non-null    object 
 11  depart            200 non-null    object 
 12  idcourse          200 non-null    int64  
 13  idbus             0 non-null      float64
 14  numerobus         0 non-null      float64
 15  precision         200 non-null    object 
 16  visibilite        200 non-null    object 
 17  heu